In [3]:
import pandas as pd
import os

In [4]:
DATA_DIR = "../data"
PROCESSED_DIR = "../processed/"
FACET_DIR = "days_on_market/"
FULL_DATA_DIR_PATH = os.path.join(DATA_DIR, FACET_DIR)
FULL_PROCESSED_DIR_PATH = os.path.join(PROCESSED_DIR, FACET_DIR)

In [7]:
data_frames = []

exclude_columns = [
    "RegionID",
    "SizeRank",
    "RegionName",
    "RegionType",
    "StateName",
    "Home Type",
]

slug_column_mappings = {
    "_mean_listings_price_cut_amt_": "Mean Listings Price Cut Amount",
    "_med_doz_pending_": "Median Days on Pending",
    "_median_days_to_pending_": "Median Days to Close",
    "_perc_listings_price_cut_": "Percent Listings Price Cut",
}


def get_df(
    df, exclude_columns, columns_to_pivot, col_name, smoothed, seasonally_adjusted
):
    if smoothed:
        col_name += " (Smoothed)"
    if seasonally_adjusted:
        col_name += " (Seasonally Adjusted)"

    df = pd.melt(
        df,
        id_vars=exclude_columns,
        value_vars=columns_to_pivot,
        var_name="Date",
        value_name=col_name,
    )
    return df


for filename in os.listdir(FULL_DATA_DIR_PATH):
    if filename.endswith(".csv"):
        # print("processing " + filename)
        cur_df = pd.read_csv(os.path.join(FULL_DATA_DIR_PATH, filename))

        # skip month files for now since they are redundant
        if "month" in filename:
            continue

        if "_uc_sfrcondo_" in filename:
            cur_df["Home Type"] = "all homes (SFR + Condo)"
            # change column type to string
            cur_df["RegionName"] = cur_df["RegionName"].astype(str)
        elif "_uc_sfr_" in filename:
            cur_df["Home Type"] = "SFR"

        # Identify columns to pivot
        columns_to_pivot = [col for col in cur_df.columns if col not in exclude_columns]

        smoothed = "_sm_" in filename
        seasonally_adjusted = "_sa_" in filename

        # iterate over slug column mappings and get df
        for slug, col_name in slug_column_mappings.items():
            if slug in filename:
                cur_df = get_df(
                    cur_df,
                    exclude_columns,
                    columns_to_pivot,
                    col_name,
                    smoothed,
                    seasonally_adjusted,
                )

                data_frames.append(cur_df)
                break


def get_combined_df(data_frames):
    combined_df = None
    if len(data_frames) > 1:
        # iterate over dataframes and merge or concat
        combined_df = data_frames[0]
        for i in range(1, len(data_frames)):
            cur_df = data_frames[i]
            combined_df = pd.merge(
                combined_df,
                cur_df,
                on=[
                    "RegionID",
                    "SizeRank",
                    "RegionName",
                    "RegionType",
                    "StateName",
                    "Home Type",
                    "Date",
                ],
                how="outer",
                suffixes=("", "_" + str(i)),
            )
    elif len(data_frames) == 1:
        combined_df = data_frames[0]

    return combined_df


combined_df = get_combined_df(data_frames)

# iterate over rows of combined df and coalesce column values across columns that start with "Median Sale Price"
columns_to_coalesce = slug_column_mappings.values()
print(columns_to_coalesce)

for index, row in combined_df.iterrows():
    for col in combined_df.columns:
        for column_to_coalesce in columns_to_coalesce:
            if column_to_coalesce in col and "_" in col:
                if not pd.isna(row[col]):
                    combined_df.at[index, column_to_coalesce] = row[col]

# remove columns with underscores
combined_df = combined_df[[col for col in combined_df.columns if "_" not in col]]

combined_df

dict_values(['Mean Listings Price Cut Amount', 'Median Days on Pending', 'Median Days to Close', 'Percent Listings Price Cut'])


RegionID  SizeRank     RegionName RegionType StateName  \
0         102001         0  United States    country       NaN   
1         102001         0  United States    country       NaN   
2         102001         0  United States    country       NaN   
3         102001         0  United States    country       NaN   
4         102001         0  United States    country       NaN   
...          ...       ...            ...        ...       ...   
586709    845172       769   Winfield, KS        msa        KS   
586710    845172       769   Winfield, KS        msa        KS   
586711    845172       769   Winfield, KS        msa        KS   
586712    845172       769   Winfield, KS        msa        KS   
586713    845172       769   Winfield, KS        msa        KS   

                      Home Type        Date  \
0                           SFR  2018-01-06   
1                           SFR  2018-01-13   
2                           SFR  2018-01-20   
3                           SFR  2018-01-27   
4                           SFR  2018-02-03   
...                         ...         ...   
586709  all homes (SFR + Condo)  2024-01-06   
586710  all homes (SFR + Condo)  2024-01-13   
586711  all homes (SFR + Condo)  2024-01-20   
586712  all homes (SFR + Condo)  2024-01-27   
586713  all homes (SFR + Condo)  2024-02-03   

        Mean Listings Price Cut Amount (Smoothed)  Percent Listings Price Cut  \
0                                             NaN                         NaN   
1                                             NaN                    0.049042   
2                                             NaN                    0.044740   
3                                             NaN                    0.047930   
4                                             NaN                    0.047622   
...                                           ...                         ...   
586709                                        NaN                    0.094017   
586710                                        NaN                    0.070175   
586711                                        NaN                    0.043478   
586712                                        NaN                    0.036697   
586713                                        NaN                    0.077670   

        Mean Listings Price Cut Amount  Percent Listings Price Cut (Smoothed)  \
0                         13508.368375                                    NaN   
1                         14114.788383                                    NaN   
2                         14326.128956                                    NaN   
3                         13998.585612                                    NaN   
4                         14120.035549                                    NaN   
...                                ...                                    ...   
586709                             NaN                               0.037378   
586710                             NaN                               0.043203   
586711                             NaN                               0.054073   
586712                             NaN                               0.061092   
586713                             NaN                               0.057005   

        Median Days on Pending (Smoothed)  Median Days on Pending  
0                                     NaN                     NaN  
1                                     NaN                     NaN  
2                                     NaN                     NaN  
3                                     NaN                     NaN  
4                                     NaN                     NaN  
...                                   ...                     ...  
586709                                NaN                     NaN  
586710                                NaN                     NaN  
586711                                NaN                     NaN  
586712                  

In [16]:
final_df = combined_df
final_df = final_df.rename(
    columns={
        "RegionID": "Region ID",
        "SizeRank": "Size Rank",
        "RegionName": "Region",
        "RegionType": "Region Type",
    }
)

final_df

Region ID  Size Rank         Region Region Type StateName  \
0          102001          0  United States     country       NaN   
1          102001          0  United States     country       NaN   
2          102001          0  United States     country       NaN   
3          102001          0  United States     country       NaN   
4          102001          0  United States     country       NaN   
...           ...        ...            ...         ...       ...   
586709     845172        769   Winfield, KS         msa        KS   
586710     845172        769   Winfield, KS         msa        KS   
586711     845172        769   Winfield, KS         msa        KS   
586712     845172        769   Winfield, KS         msa        KS   
586713     845172        769   Winfield, KS         msa        KS   

                      Home Type        Date  \
0                           SFR  2018-01-06   
1                           SFR  2018-01-13   
2                           SFR  2018-01-20   
3                           SFR  2018-01-27   
4                           SFR  2018-02-03   
...                         ...         ...   
586709  all homes (SFR + Condo)  2024-01-06   
586710  all homes (SFR + Condo)  2024-01-13   
586711  all homes (SFR + Condo)  2024-01-20   
586712  all homes (SFR + Condo)  2024-01-27   
586713  all homes (SFR + Condo)  2024-02-03   

        Mean Listings Price Cut Amount (Smoothed)  Percent Listings Price Cut  \
0                                             NaN                         NaN   
1                                             NaN                    0.049042   
2                                             NaN                    0.044740   
3                                             NaN                    0.047930   
4                                             NaN                    0.047622   
...                                           ...                         ...   
586709                                        NaN                    0.094017   
586710                                        NaN                    0.070175   
586711                                        NaN                    0.043478   
586712                                        NaN                    0.036697   
586713                                        NaN                    0.077670   

        Mean Listings Price Cut Amount  Percent Listings Price Cut (Smoothed)  \
0                         13508.368375                                    NaN   
1                         14114.788383                                    NaN   
2                         14326.128956                                    NaN   
3                         13998.585612                                    NaN   
4                         14120.035549                                    NaN   
...                                ...                                    ...   
586709                             NaN                               0.037378   
586710                             NaN                               0.043203   
586711                             NaN                               0.054073   
586712                             NaN                               0.061092   
586713                             NaN                               0.057005   

        Median Days on Pending (Smoothed)  Median Days on Pending  
0                                     NaN                     NaN  
1                                     NaN                     NaN  
2                                     NaN                     NaN  
3                                     NaN                     NaN  
4                                     NaN                     NaN  
...                                   ...                     ...  
586709                                NaN                     NaN  
586710                                NaN                     NaN  
586711                                NaN               

In [15]:
if not os.path.exists(FULL_PROCESSED_DIR_PATH):
    os.makedirs(FULL_PROCESSED_DIR_PATH)

final_df.to_json(FULL_PROCESSED_DIR_PATH + "final.jsonl", orient="records", lines=True)